# Imports

In [1]:
import ee
import numpy as np
import math
import geemap
import geopandas as gpd
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats

In [2]:
#ee.Authenticate()


In [3]:

# Initialize Google Earth Engine
ee.Initialize()

In [4]:
nm_path = r"C:\Users\bsf31\Documents\post-meds\data\signal\climate\NM\nm_vector.gpkg"
study_boundary = gpd.read_file(nm_path, layer='counties_dissolved')
hurley_gdf = gpd.read_file(nm_path, layer='north_hurley')

In [5]:
# Convert to Earth Engine geometry
ee_boundary = geemap.geopandas_to_ee(study_boundary)

ee_hurley = geemap.geopandas_to_ee(hurley_gdf).geometry()


In [6]:
ee_boundary_coordinates = ee_boundary.geometry()

# Landsat Collection 2

In [7]:
# Function to scale the surface temperature band and convert to Fahrenheit
def scale_lst(image):
    lst_k = image.select('ST_B10').multiply(0.00341802).add(149.0)
    lst_f = lst_k.subtract(273.15).multiply(1.8).add(32)
    return image.addBands(lst_f.rename('LST_F'))

# Function to calculate NDVI
def calculate_ndvi(image):
    ndvi = image.normalizedDifference(['SR_B5', 'SR_B4'])
    return image.addBands(ndvi.rename('NDVI'))

# Function to calculate Fraction of Vegetation Cover
def calculate_fvc(image):
    fvc = image.select('NDVI').subtract(0.2).divide(0.3).pow(2).clamp(0, 1)
    return image.addBands(fvc.rename('FVC'))

# Function to calculate Emissivity
def calculate_emissivity(image):
    emissivity = image.select('FVC').multiply(0.0004).add(0.986)
    return image.addBands(emissivity.rename('Emissivity'))

# Define a function to clip each image to the ROI
def clip_to_region(image,roi):
    return image.clip(roi)


In [8]:
pt = ee.Geometry.Point([-108.13, 32.70])   # Point corresponding to Santa Barbara, CA
start_date = '2019-04-01'
end_date = '2024-11-01'

# Load the Landsat 8 collection and filter images based on criteria
landsat_collection = ee.ImageCollection("LANDSAT/LC08/C02/T1_L2") \
    .filterDate(start_date, end_date) \
    .filter(ee.Filter.calendarRange(5, 10, 'month')) \
    .filterBounds(pt)\
    .filter(ee.Filter.lt('CLOUD_COVER', 10))  # Filter for images with less than 10% cloud cover

In [9]:
# Get the list of image dates that meet the criteria
image_dates = landsat_collection.aggregate_array('system:time_start').map(lambda t: ee.Date(t).format('YYYY-MM-dd')).getInfo()

print("Selected Image Dates:")
print(image_dates)

Selected Image Dates:
['2019-05-29', '2019-06-30', '2019-08-01', '2019-09-02', '2019-09-18', '2019-10-20', '2020-05-15', '2020-05-31', '2020-06-16', '2020-08-03', '2020-08-19', '2020-09-04', '2020-09-20', '2020-10-06', '2020-10-22', '2021-05-02', '2021-06-03', '2021-06-19', '2021-07-21', '2021-08-06', '2021-08-22', '2021-09-07', '2021-10-09', '2021-10-25', '2022-05-05', '2022-05-21', '2022-06-06', '2022-07-08', '2022-09-10', '2022-10-12', '2022-10-28', '2023-05-08', '2023-05-24', '2023-06-25', '2023-07-27', '2023-09-29', '2023-10-15', '2023-10-31', '2024-05-10', '2024-05-26', '2024-06-11', '2024-07-13', '2024-08-14', '2024-08-30', '2024-10-01']


In [10]:
# Apply all processing steps
processed_collection = landsat_collection \
    .map(lambda image: image.clip(ee_hurley)) \
    .map(scale_lst) \
    .map(calculate_ndvi) \
    .map(calculate_fvc) \
    .map(calculate_emissivity) 


In [11]:
processed_collection

In [12]:
# Function to extract LST values
def extract_lst(image):
    date = ee.Date(image.get('system:time_start')).format('YYYY-MM-dd')
    mean_lst = image.select('LST_F').reduceRegion(
        reducer=ee.Reducer.mean(),
        geometry=ee_hurley,
        scale=30
    ).get('LST_F')
    return ee.Feature(None, {'date': date, 'LST': mean_lst})

# Extract LST values
lst_values = processed_collection.map(extract_lst)


In [13]:
# Print results
print("Date, Mean LST (°F)")
lst_list = lst_values.getInfo().get('features')
for feature in lst_list:
    date = feature['properties']['date']
    lst = feature['properties']['LST']
    print(f"{date}, {lst:.2f}")

# Print collection information
print(f"\nNumber of images: {processed_collection.size().getInfo()}")
print(f"Date range: {start_date} to {end_date}")

# Print cloud cover information
cloud_covers = processed_collection.aggregate_array('CLOUD_COVER').getInfo()
dates = processed_collection.aggregate_array('system:time_start').getInfo()
dates = [ee.Date(d).format('YYYY-MM-dd').getInfo() for d in dates]

print("\nCloud cover for each image:")
for date, cloud_cover in zip(dates, cloud_covers):
    print(f"{date}: {cloud_cover:.2f}%")

Date, Mean LST (°F)
2019-05-29, 115.36
2019-06-30, 119.21
2019-08-01, 111.59
2019-09-02, 113.21
2019-09-18, 92.38
2019-10-20, 83.49
2020-05-15, 111.84
2020-05-31, 116.87
2020-06-16, 119.08
2020-08-03, 128.26
2020-08-19, 122.50
2020-09-04, 119.79
2020-09-20, 108.93
2020-10-06, 108.90
2020-10-22, 98.24
2021-05-02, 110.48
2021-06-03, 126.90
2021-06-19, 141.24
2021-07-21, 131.04
2021-08-06, 113.32
2021-08-22, 106.04
2021-09-07, 103.65
2021-10-09, 97.02
2021-10-25, 94.03
2022-05-05, 116.54
2022-05-21, 123.21
2022-06-06, 130.63
2022-07-08, 122.72
2022-09-10, 111.20
2022-10-12, 88.80
2022-10-28, 75.84
2023-05-08, 119.40
2023-05-24, 116.72
2023-06-25, 130.66
2023-07-27, 137.41
2023-09-29, 106.03
2023-10-15, 98.15
2023-10-31, 69.84
2024-05-10, 111.42
2024-05-26, 119.21
2024-06-11, 130.54
2024-07-13, 122.06
2024-08-14, 104.32
2024-08-30, 114.00
2024-10-01, 110.11

Number of images: 45
Date range: 2019-04-01 to 2024-11-01

Cloud cover for each image:
2019-05-29: 7.42%
2019-06-30: 7.17%
2019-08-01

In [25]:
## Define the specific dates you want to inspect
specific_dates = ['2019-09-18', '2024-08-14']  # Replace with your desired dates

# Filter the collection for specific dates using ee.Filter.Or
filtered_collection = processed_collection.filter(
    ee.Filter.Or(
        ee.Filter.date(specific_dates[0], ee.Date(specific_dates[0]).advance(1, 'day')),
        ee.Filter.date(specific_dates[1], ee.Date(specific_dates[1]).advance(1, 'day'))
    )
)

# Check if the collection is empty
if filtered_collection.size().getInfo() == 0:
    raise ValueError("No images found for the specified dates.")

# Create the map and add true-color layers for the specific dates
Map = geemap.Map()
Map.center_object(ee_hurley, 12)

# Visualization parameters for true-color composite
true_color_vis_params = {
    'bands': ['SR_B4', 'SR_B3', 'SR_B2'],  # Red, Green, Blue
    'min': 0,
    'max': 3000,  # Adjust based on the reflectance range of your data
    'gamma': 1.4  # Optional: adjust for better visualization
}

# Add true-color layers for each date
filtered_images = filtered_collection.toList(filtered_collection.size())
for i in range(filtered_collection.size().getInfo()):
    image = ee.Image(filtered_images.get(i))
    image_date = ee.Date(image.get('system:time_start')).format('YYYY-MM-dd').getInfo()
    Map.addLayer(image, true_color_vis_params, f'True Color {image_date}')

Map.addLayer(ee_hurley, {}, 'Hurley Boundary')
Map





Map(center=[32.72611641066423, -108.13061907314244], controls=(WidgetControl(options=['position', 'transparent…

In [15]:
# Calculate the mean image across the entire collection
collection_mean = processed_collection.mean()

# Extract the mean LST over the Hurley area
mean_lst = collection_mean.select('LST_F').reduceRegion(
    reducer=ee.Reducer.mean(),
    geometry=ee_hurley,
    scale=30,
    maxPixels=1e8,
    bestEffort=True
).get('LST_F')

# Get the result as a Python object
mean_lst_value = mean_lst.getInfo()

print("Mean LST (°F) for the entire collection over Hurley, NM:", mean_lst_value)


Mean LST (°F) for the entire collection over Hurley, NM: 112.28109599784102


In [16]:
# Set up export parameters
export_task = ee.batch.Export.image.toDrive(
    image=collection_mean.select('LST_F'),  # Select the LST band
    description='North_Hurley_LST_Mean',
    folder='lst',  # Optional: specify a folder in Google Drive
    fileNamePrefix='North_Hurley_LST_Mean_Image',
    region=ee_hurley,
    scale=30,
    crs='EPSG:4326',  # 'EPSG:32612',  # Use UTM Zone 12N to match the Hurley vectors
    maxPixels=1e13
)

# Start the export task
export_task.start()
print("Exporting mean LST image to Google Drive...")

Exporting mean LST image to Google Drive...


In [ ]:
Map = geemap.Map()
Map.center_object(ee_hurley, 12)
Map.addLayer(collection_mean, {}, 'collection_mean')
Map


Map(center=[32.72611641066423, -108.13061907314244], controls=(WidgetControl(options=['position', 'transparent…

In [18]:
# Function to calculate per-image statistics for LST
def calculate_stats_per_image(image):
    stats = image.select('LST_F').reduceRegion(
        reducer=ee.Reducer.mean()
            .combine(ee.Reducer.min(), sharedInputs=True)
            .combine(ee.Reducer.max(), sharedInputs=True)
            .combine(ee.Reducer.stdDev(), sharedInputs=True),
        geometry=ee_hurley,
        scale=30,
        maxPixels=1e8,
        bestEffort=True
    )
    return image.set(stats)

In [19]:
# Apply the function to each image in the collection to get per-image statistics
stats_per_image = processed_collection.map(calculate_stats_per_image)

In [20]:
stats_per_image

In [21]:
# Extract individual statistics
dates = stats_per_image.aggregate_array('system:time_start').getInfo()
means = stats_per_image.aggregate_array('LST_F_mean').getInfo()
mins = stats_per_image.aggregate_array('LST_F_min').getInfo()
maxs = stats_per_image.aggregate_array('LST_F_max').getInfo()
std_devs = stats_per_image.aggregate_array('LST_F_stdDev').getInfo()


In [22]:
# Print per-image statistics
print("Per-image LST statistics:")
for date, mean, min_, max_, std_dev in zip(dates, means, mins, maxs, std_devs):
    formatted_date = ee.Date(date).format("YYYY-MM-dd").getInfo()
    print(f"Date: {formatted_date}, Mean LST: {mean}, Min LST: {min_}, Max LST: {max_}, StdDev LST: {std_dev}")

Per-image LST statistics:
Date: 2019-05-29, Mean LST: 115.35901257824831, Min LST: 110.87300991200004, Max LST: 119.36337159200005, StdDev LST: 2.217503900018814
Date: 2019-06-30, Mean LST: 119.21010768644243, Min LST: 114.36144112400002, Max LST: 123.35630255600005, StdDev LST: 2.023470770866674
Date: 2019-08-01, Mean LST: 111.5860255203805, Min LST: 104.89899455600008, Max LST: 116.53325103200005, StdDev LST: 2.50183849038396
Date: 2019-09-02, Mean LST: 113.20688710192464, Min LST: 106.0125854720001, Max LST: 117.78219554000009, StdDev LST: 2.238136856356755
Date: 2019-09-18, Mean LST: 92.37793032866563, Min LST: 76.61009382799996, Max LST: 101.07217936400004, StdDev LST: 4.974893415040123
Date: 2019-10-20, Mean LST: 83.48965699305798, Min LST: 79.12028771600004, Max LST: 85.95564411200003, StdDev LST: 1.0949781808670866
Date: 2020-05-15, Mean LST: 111.83893493949964, Min LST: 107.01543254000008, Max LST: 115.77034896800008, StdDev LST: 1.7161852119102514
Date: 2020-05-31, Mean LST: 

In [23]:
# Calculate overall statistics for the entire collection (min, max, stdDev)
collection_min = processed_collection.select('LST_F').reduce(ee.Reducer.min()).reduceRegion(
    reducer=ee.Reducer.mean(),
    geometry=ee_hurley,
    scale=30,
    maxPixels=1e8,
    bestEffort=True
).getInfo()

collection_max = processed_collection.select('LST_F').reduce(ee.Reducer.max()).reduceRegion(
    reducer=ee.Reducer.mean(),
    geometry=ee_hurley,
    scale=30,
    maxPixels=1e8,
    bestEffort=True
).getInfo()

collection_stddev = processed_collection.select('LST_F').reduce(ee.Reducer.stdDev()).reduceRegion(
    reducer=ee.Reducer.mean(),
    geometry=ee_hurley,
    scale=30,
    maxPixels=1e8,
    bestEffort=True
).getInfo()

# Print overall statistics
print("\nOverall Collection Statistics:")
print(f"Min LST: {collection_min}")
print(f"Max LST: {collection_max}")
print(f"StdDev LST: {collection_stddev}")


Overall Collection Statistics:
Min LST: {'LST_F_min': 69.53084329279976}
Max LST: {'LST_F_max': 141.25305187650108}
StdDev LST: {'LST_F_stdDev': 15.351702002917154}


Per-Image Standard Deviation: For each image, the standard deviation shows the variability of LST across the Hurley area at a specific time. A low standard deviation means the temperatures are relatively uniform across the region, while a high standard deviation suggests there are large differences in temperature within that image, perhaps due to mixed land covers or varying microclimates.

Overall Collection Standard Deviation: When calculated across the entire collection, the standard deviation reflects how much the mean LST changes over time. A low value indicates that the temperatures are fairly stable across the whole period, while a high standard deviation suggests significant temperature changes over time, such as seasonal variations or extreme weather events.

In [26]:
# Create the DataFrame
data = {
    'Date': [ee.Date(date).format("YYYY-MM-dd").getInfo() for date in dates],
    'Mean_LST': means,
    'Min_LST': mins,
    'Max_LST': maxs,
    'StdDev_LST': std_devs
}
df = pd.DataFrame(data)
df['Date'] = pd.to_datetime(df['Date'])

# Overall collection statistics
overall_min = 69.53 
overall_max = 141.25 
overall_std_dev = 15.35 
overall_mean = 112.28  

# Set up the scatter plot
plt.figure(figsize=(14, 8))
sns.scatterplot(x='Date', y='Mean_LST', data=df, color='blue', label='Mean LST')

# Add error bars for standard deviation
plt.errorbar(df['Date'], df['Mean_LST'], yerr=df['StdDev_LST'], fmt='o', ecolor='gray', alpha=0.5, capsize=3)

# Add shaded area for Min-Max range
plt.fill_between(df['Date'], df['Min_LST'], df['Max_LST'], color='blue', alpha=0.2, label='Min-Max Range')

# Add overall statistics as horizontal lines
plt.axhline(overall_min, color='green', linestyle='--', label=f'average of the Min LST: {overall_min:.2f} °F')
plt.axhline(overall_max, color='red', linestyle='--', label=f'average of the Max LST: {overall_max:.2f} °F')
plt.axhline(overall_mean, color='orange', linestyle='--', label=f'average of the Mean LST: {overall_mean:.2f} °F')
plt.axhline(overall_mean + overall_std_dev, color='purple', linestyle='--', alpha=0.5, label=f'average of the Mean ± Std Dev(15.85)')
plt.axhline(overall_mean - overall_std_dev, color='purple', linestyle='--', alpha=0.5)

# Customize the plot
plt.xlabel('Date')
plt.ylabel('LST (°F)')
plt.title('Land Surface Temperature (LST) in Hurley, NM Over Time')
plt.legend()
plt.grid(True)
plt.xticks(rotation=45)
plt.tight_layout()

# Show the plot
plt.show()